In [1]:
import numpy as np
import pandas as pd

import seaborn as sns
import matplotlib.pyplot as plt
sns.set_style("white")
%matplotlib inline

from matplotlib.ticker import FuncFormatter

import plotly.express as px
import plotly.graph_objects as go

C:\Users\erinm\Anaconda3\lib\site-packages\statsmodels\tools\_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


In [86]:
plt.rc('font', size=22)          
plt.rc('axes', labelsize=28)    
plt.rc('figure', titlesize=44)
plt.rcParams['font.sans-serif'] = "Lucida Sans Unicode"

In [140]:
donations13to17=pd.read_feather('donations13to17.ftr')

In [141]:
#keep only relevant columnns from full dataset
amounts1=donations13to17[['id','cohort','yr0','yr1','amount_yr0','amount_yr1']].copy().sort_values('amount_yr0').reset_index(drop=True)

In [142]:
amounts1['retention_yr1']=amounts1['yr1']/amounts1['yr0']

### Isolate cohort13

In [143]:
c13=amounts1.query('cohort=="cohort13"')

In [144]:
c13['yr1'].sum()/c13['yr0'].sum()

0.19411439408377568

### groups

In [145]:
#1024 groups
c13.loc[:,'group1024']=pd.qcut(c13.index, q=1024, labels=False)

C:\Users\erinm\Anaconda3\lib\site-packages\pandas\core\indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\erinm\Anaconda3\lib\site-packages\pandas\core\indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [146]:
#2048 groups
c13.loc[:,'group2048']=pd.qcut(c13.index, q=2048, labels=False)

In [147]:
#4096 groups
c13.loc[:,'group4096']=pd.qcut(c13.index, q=4096, labels=False)

In [148]:
#8192 groups
c13.loc[:,'group8192']=pd.qcut(c13.index, q=8192, labels=False)

### groupby group8192

In [149]:
df=c13.groupby(['group8192']).agg({'yr0':'sum','yr1':'sum','retention_yr1':'mean'}).reset_index()

In [152]:
c13

id    cohort  yr0  yr1  amount_yr0  \
5        69a7c6fed3094256c371fdd946585c15  cohort13    1    0        0.40   
8        2bb12d73c1b7859ad4e045ad455a03c3  cohort13    1    0        1.00   
9        54738e4163f3a49cc6f405c1ef221b26  cohort13    1    0        1.00   
11       e9c19a42c4965f0f91262bd56ff98cda  cohort13    1    0        1.00   
12       a614620bb7ac42c58e6740bdddf420e9  cohort13    1    0        1.00   
...                                   ...       ...  ...  ...         ...   
1876458  2144d56b1947ebb26a19e7f1d07c970a  cohort13    1    1    90140.60   
1876459  96c4f21513cd8962acb147ab384e6434  cohort13    1    1    94901.50   
1876463  0e01e632606c230914fe73c2d2ccead3  cohort13    1    1   113360.94   
1876465  8f70fc7370842e0709cd9af3d29b4b0b  cohort13    1    1   163192.85   
1876466  a0e1d358aa17745ff3d3f4e4909356f3  cohort13    1    1   442794.38   

         amount_yr1  retention_yr1  group1024  group2048  group4096  group8192  
5              0.00            0.0          0          0          0          0  
8              0.00            0.0          0          0          0          0  
9              0.00            0.0          0          0          0          0  
11             0.00            0.0          0          0          0          0  
12             0.00            0.0          0          0          0          0  
...             ...            ...        ...        ...        ...        ...  
1876458   159344.38            1.0       1023       2047       4095       8191  
1876459   215995.85            1.0       1023       2047       4095       8191  
1876463    77656.30            1.0       1023       2047       4095       8191  
1876465    30893.09            1.0       1023       2047       4095       8191  
1876466   570161.90            1.0       1023       2047       4095       8191  

[320069 rows x 11 columns]

In [150]:
df

group8192  yr0  yr1  retention_yr1
0             0   40    0       0.000000
1             1   39    3       0.076923
2             2   39    1       0.025641
3             3   39    3       0.076923
4             4   39    3       0.076923
...         ...  ...  ...            ...
8187       8187   39   21       0.538462
8188       8188   39   25       0.641026
8189       8189   39   23       0.589744
8190       8190   39   15       0.384615
8191       8191   40   28       0.700000

[8192 rows x 4 columns]

### identify min/max of each group and create column showing bounds

In [151]:
dfc=c13.groupby('group8192')['amount_yr0']

In [153]:
dfc1=c13.assign(min=dfc.transform(min), max=dfc.transform(max))

In [154]:
dfc1['group_range']=dfc1['min'].astype(str) + " - " + dfc1['max'].astype(str)

In [155]:
df1=dfc1.groupby(['group8192','group_range']).count()['id'].reset_index()

In [156]:
dfc1['cohort_overall_retention']=dfc1.retention_yr1.mean()

In [157]:
dfc1

id    cohort  yr0  yr1  amount_yr0  \
5        69a7c6fed3094256c371fdd946585c15  cohort13    1    0        0.40   
8        2bb12d73c1b7859ad4e045ad455a03c3  cohort13    1    0        1.00   
9        54738e4163f3a49cc6f405c1ef221b26  cohort13    1    0        1.00   
11       e9c19a42c4965f0f91262bd56ff98cda  cohort13    1    0        1.00   
12       a614620bb7ac42c58e6740bdddf420e9  cohort13    1    0        1.00   
...                                   ...       ...  ...  ...         ...   
1876458  2144d56b1947ebb26a19e7f1d07c970a  cohort13    1    1    90140.60   
1876459  96c4f21513cd8962acb147ab384e6434  cohort13    1    1    94901.50   
1876463  0e01e632606c230914fe73c2d2ccead3  cohort13    1    1   113360.94   
1876465  8f70fc7370842e0709cd9af3d29b4b0b  cohort13    1    1   163192.85   
1876466  a0e1d358aa17745ff3d3f4e4909356f3  cohort13    1    1   442794.38   

         amount_yr1  retention_yr1  group1024  group2048  group4096  \
5              0.00            0.0          0          0          0   
8              0.00            0.0          0          0          0   
9              0.00            0.0          0          0          0   
11             0.00            0.0          0          0          0   
12             0.00            0.0          0          0          0   
...             ...            ...        ...        ...        ...   
1876458   159344.38            1.0       1023       2047       4095   
1876459   215995.85            1.0       1023       2047       4095   
1876463    77656.30            1.0       1023       2047       4095   
1876465    30893.09            1.0       1023       2047       4095   
1876466   570161.90            1.0       1023       2047       4095   

         group8192       min        max           group_range  \
5                0      0.40       1.00             0.4 - 1.0   
8                0      0.40       1.00             0.4 - 1.0   
9                0      0.40       1.00             0.4 - 1.0   
11               0      0.40       1.00             0.4 - 1.0   
12               0      0.40       1.00             0.4 - 1.0   
...            ...       ...        ...                   ...   
1876458       8191  21080.02  442794.38  21080.02 - 442794.38   
1876459       8191  21080.02  442794.38  21080.02 - 442794.38   
1876463       8191  21080.02  442794.38  21080.02 - 442794.38   
1876465       8191  21080.02  442794.38  21080.02 - 442794.38   
1876466       8191  21080.02  442794.38  21080.02 - 442794.38   

         cohort_overall_retention  
5                        0.194114  
8                        0.194114  
9                        0.194114  
11                       0.194114  
12                       0.194114  
...                           ...  
1876458                  0.194114  
1876459                  0.194114  
1876463                  0.194114  
1876465                  0.194114  
1876466                  0.194114  

[320069 rows x 15 columns]

### inspect frequency of group range amounts

In [158]:
df2=df1.groupby('group_range').count().reset_index()

In [159]:
df2

group_range  group8192   id
0              0.4 - 1.0          1    1
1              1.0 - 1.0        241  241
2             1.0 - 1.15          1    1
3            1.19 - 1.86          1    1
4             1.91 - 2.0          1    1
...                  ...        ...  ...
1123       99.66 - 99.82          1    1
1124       99.82 - 99.99          1    1
1125       99.99 - 100.0          1    1
1126     996.79 - 1000.0          1    1
1127  9999.98 - 11162.24          1    1

[1128 rows x 3 columns]

In [160]:
df2.sort_values('group8192',ascending=False)

group_range  group8192    id
458          25.0 - 25.0       1660  1660
799          50.0 - 50.0       1317  1317
5            10.0 - 10.0        950   950
345          20.0 - 20.0        802   802
10         100.0 - 100.0        707   707
...                  ...        ...   ...
396         22.5 - 22.71          1     1
397        22.72 - 22.95          1     1
398         22.96 - 23.0          1     1
400       220.0 - 220.39          1     1
1127  9999.98 - 11162.24          1     1

[1128 rows x 3 columns]

In [161]:
fig = px.bar(df2.query('id > 10'), x='group_range', y='id')
fig.show()

In [162]:
df2.query('group8192 > 3')

group_range  group8192    id
1         1.0 - 1.0        241   241
5       10.0 - 10.0        950   950
10    100.0 - 100.0        707   707
33    105.0 - 105.0          5     5
56    110.0 - 110.0         14    14
75    115.0 - 115.0          6     6
94      12.0 - 12.0          4     4
98    120.0 - 120.0         13    13
115   125.0 - 125.0         53    53
135   130.0 - 130.0          6     6
150   135.0 - 135.0          4     4
169   140.0 - 140.0          6     6
198     15.0 - 15.0        100   100
204   150.0 - 150.0         84    84
233   160.0 - 160.0          5     5
275   175.0 - 175.0         11    11
287     18.0 - 18.0          6     6
341       2.0 - 2.0         70    70
345     20.0 - 20.0        802   802
351   200.0 - 200.0         97    97
407   225.0 - 225.0          7     7
458     25.0 - 25.0       1660  1660
464   250.0 - 250.0         24    24
545       3.0 - 3.0         23    23
549     30.0 - 30.0        131   131
554   300.0 - 300.0         24    24
622     35.0 - 35.0         53    53
635     36.0 - 36.0          6     6
682       4.0 - 4.0         12    12
686     40.0 - 40.0        108   108
692   400.0 - 400.0          8     8
740     45.0 - 45.0         34    34
795       5.0 - 5.0        158   158
799     50.0 - 50.0       1317  1317
804   500.0 - 500.0         16    16
847     55.0 - 55.0         17    17
885       6.0 - 6.0          4     4
889     60.0 - 60.0         45    45
924     65.0 - 65.0         14    14
959     70.0 - 70.0         26    26
989     75.0 - 75.0        159   159
1021    80.0 - 80.0         18    18
1046    85.0 - 85.0          9     9
1076    90.0 - 90.0         13    13
1098    95.0 - 95.0          8     8

In [163]:
#group8192 yields groups with 1128 distinct ranges


In [164]:
dfc1.groupby('group_range').count()['group8192'].reset_index().sort_values('group8192', ascending=False)

group_range  group8192
458          25.0 - 25.0      64858
799          50.0 - 50.0      51456
5            10.0 - 10.0      37117
345          20.0 - 20.0      31335
10         100.0 - 100.0      27623
...                  ...        ...
474       258.0 - 258.84         39
475       258.88 - 260.0         39
84         117.5 - 118.0         39
477         26.0 - 26.13         39
1127  9999.98 - 11162.24         39

[1128 rows x 2 columns]

In [165]:
dfc1.group_range.value_counts(normalize=True)

25.0 - 25.0        0.202638
50.0 - 50.0        0.160765
10.0 - 10.0        0.115966
20.0 - 20.0        0.097901
100.0 - 100.0      0.086303
                     ...   
696.41 - 700.0     0.000122
98.12 - 98.42      0.000122
28.52 - 28.79      0.000122
390.0 - 392.2      0.000122
317.68 - 318.82    0.000122
Name: group_range, Length: 1128, dtype: float64

In [166]:
df=dfc1.groupby(['group8192','group_range','cohort_overall_retention']).agg({'yr0':'sum','yr1':'sum','retention_yr1':'mean'}).reset_index()

df['group']=df['group8192'].astype(str)

df['comparative_retention']=np.where(df['retention_yr1']>df['cohort_overall_retention'],"higher",'lower')

In [167]:
df

group8192           group_range  cohort_overall_retention  yr0  yr1  \
0             0             0.4 - 1.0                  0.194114   40    0   
1             1             1.0 - 1.0                  0.194114   39    3   
2             2             1.0 - 1.0                  0.194114   39    1   
3             3             1.0 - 1.0                  0.194114   39    3   
4             4             1.0 - 1.0                  0.194114   39    3   
...         ...                   ...                       ...  ...  ...   
8187       8187     8947.25 - 9999.04                  0.194114   39   21   
8188       8188    9999.98 - 11162.24                  0.194114   39   25   
8189       8189   11313.05 - 14182.79                  0.194114   39   23   
8190       8190    14183.44 - 20385.0                  0.194114   39   15   
8191       8191  21080.02 - 442794.38                  0.194114   40   28   

      retention_yr1 group comparative_retention  
0          0.000000     0                 lower  
1          0.076923     1                 lower  
2          0.025641     2                 lower  
3          0.076923     3                 lower  
4          0.076923     4                 lower  
...             ...   ...                   ...  
8187       0.538462  8187                higher  
8188       0.641026  8188                higher  
8189       0.589744  8189                higher  
8190       0.384615  8190                higher  
8191       0.700000  8191                higher  

[8192 rows x 8 columns]

In [168]:
df.comparative_retention.value_counts(normalize=True)

lower     0.613281
higher    0.386719
Name: comparative_retention, dtype: float64

In [169]:
df.groupby('comparative_retention').sum()[['yr0','yr1']]

yr0    yr1
comparative_retention               
higher                 123793  38922
lower                  196276  23208

In [170]:
df1=df.groupby('group_range').agg({'cohort_overall_retention': 'mean', 'yr0':'sum', 'yr1':'sum','retention_yr1':'sum'}).reset_index()

In [171]:
df1['comparative_retention']=np.where(df1['retention_yr1']>df1['cohort_overall_retention'],"higher",'lower')

In [172]:
df1['retention_diff']=df1['cohort_overall_retention']-df1['retention_yr1']

In [173]:
df1.sort_values('retention_diff')

group_range  cohort_overall_retention    yr0   yr1  retention_yr1  \
458    25.0 - 25.0                  0.194114  64858  9728     248.988462   
799    50.0 - 50.0                  0.194114  51456  8587     219.753846   
10   100.0 - 100.0                  0.194114  27623  5468     139.965385   
5      10.0 - 10.0                  0.194114  37117  4572     117.001923   
345    20.0 - 20.0                  0.194114  31335  3244      83.041667   
..             ...                       ...    ...   ...            ...   
435    24.0 - 24.0                  0.194114     39     2       0.051282   
752   46.5 - 46.77                  0.194114     39     2       0.051282   
346   20.0 - 20.05                  0.194114     39     1       0.025641   
318   19.99 - 20.0                  0.194114     39     1       0.025641   
0        0.4 - 1.0                  0.194114     40     0       0.000000   

    comparative_retention  retention_diff  
458                higher     -248.794347  
799                higher     -219.559732  
10                 higher     -139.771270  
5                  higher     -116.807809  
345                higher      -82.847552  
..                    ...             ...  
435                 lower        0.142832  
752                 lower        0.142832  
346                 lower        0.168473  
318                 lower        0.168473  
0                   lower        0.194114  

[1128 rows x 7 columns]

In [174]:
df1.query('retention_diff > 0')

group_range  cohort_overall_retention  yr0  yr1  retention_yr1  \
0         0.4 - 1.0                  0.194114   40    0       0.000000   
2        1.0 - 1.15                  0.194114   39    2       0.051282   
4        1.91 - 2.0                  0.194114   39    5       0.128205   
6      10.0 - 10.19                  0.194114   39    5       0.128205   
7     10.19 - 10.52                  0.194114   39    7       0.179487   
...             ...                       ...  ...  ...            ...   
1074    9.09 - 9.63                  0.194114   39    4       0.102564   
1104    96.0 - 96.0                  0.194114   39    7       0.179487   
1108    97.0 - 97.0                  0.194114   39    6       0.153846   
1121  99.26 - 99.47                  0.194114   39    7       0.179487   
1125  99.99 - 100.0                  0.194114   39    6       0.153846   

     comparative_retention  retention_diff  
0                    lower        0.194114  
2                    lower        0.142832  
4                    lower        0.065909  
6                    lower        0.065909  
7                    lower        0.014627  
...                    ...             ...  
1074                 lower        0.091550  
1104                 lower        0.014627  
1108                 lower        0.040268  
1121                 lower        0.014627  
1125                 lower        0.040268  

[148 rows x 7 columns]

In [175]:
df1

group_range  cohort_overall_retention   yr0  yr1  retention_yr1  \
0              0.4 - 1.0                  0.194114    40    0       0.000000   
1              1.0 - 1.0                  0.194114  9416  379       9.698718   
2             1.0 - 1.15                  0.194114    39    2       0.051282   
3            1.19 - 1.86                  0.194114    39    8       0.205128   
4             1.91 - 2.0                  0.194114    39    5       0.128205   
...                  ...                       ...   ...  ...            ...   
1123       99.66 - 99.82                  0.194114    39   17       0.435897   
1124       99.82 - 99.99                  0.194114    39    9       0.230769   
1125       99.99 - 100.0                  0.194114    39    6       0.153846   
1126     996.79 - 1000.0                  0.194114    39   17       0.435897   
1127  9999.98 - 11162.24                  0.194114    39   25       0.641026   

     comparative_retention  retention_diff  
0                    lower        0.194114  
1                   higher       -9.504604  
2                    lower        0.142832  
3                   higher       -0.011014  
4                    lower        0.065909  
...                    ...             ...  
1123                higher       -0.241783  
1124                higher       -0.036655  
1125                 lower        0.040268  
1126                higher       -0.241783  
1127                higher       -0.446911  

[1128 rows x 7 columns]

In [176]:
fig = px.bar(df1.query('retention_diff > 0'), x='group_range', y='retention_diff',
             title="Year 0 Amount Ranges with Lower than Average Retention Rates")
fig.show()

In [177]:
fig = px.scatter(df1.query('retention_diff < 0'), x='group_range', y='retention_diff',
             title="Year 0 Amount Ranges with Greater than Average Retention Rates")
fig.show()

In [178]:
df1.query('retention_diff < .1 & retention_diff > 0')

group_range  cohort_overall_retention  yr0  yr1  retention_yr1  \
4         1.91 - 2.0                  0.194114   39    5       0.128205   
6       10.0 - 10.19                  0.194114   39    5       0.128205   
7      10.19 - 10.52                  0.194114   39    7       0.179487   
8      10.53 - 10.95                  0.194114   39    7       0.179487   
20    101.66 - 102.0                  0.194114   39    6       0.153846   
...              ...                       ...  ...  ...            ...   
1074     9.09 - 9.63                  0.194114   39    4       0.102564   
1104     96.0 - 96.0                  0.194114   39    7       0.179487   
1108     97.0 - 97.0                  0.194114   39    6       0.153846   
1121   99.26 - 99.47                  0.194114   39    7       0.179487   
1125   99.99 - 100.0                  0.194114   39    6       0.153846   

     comparative_retention  retention_diff  
4                    lower        0.065909  
6                    lower        0.065909  
7                    lower        0.014627  
8                    lower        0.014627  
20                   lower        0.040268  
...                    ...             ...  
1074                 lower        0.091550  
1104                 lower        0.014627  
1108                 lower        0.040268  
1121                 lower        0.014627  
1125                 lower        0.040268  

[130 rows x 7 columns]

In [179]:
fig = px.scatter(df1, x=df1.index, y="retention_yr1", color="comparative_retention", 
             width=1000, height=400, template='simple_white',
                # size='petal_length', 
             hover_data=['group_range']
                )
fig.show()

In [180]:
fig = px.scatter(df, x="group_range", y="retention_yr1", color="comparative_retention", width=1000, height=400, template='simple_white',
                # size='petal_length', 
             hover_data=['group_range']
                )
fig.show()

In [181]:
N = 100000
fig = go.Figure(data=go.Scattergl(
    x=df["group_range"], y=df["retention_yr1"],
    mode='markers',
    marker=dict(
        size=6,
        color=np.random.randn(N),
        colorscale='Bluered',
        #line_width=.5
    )
))

# fig.update_traces(marker=dict(size=12,
#                               line=dict(width=2,
#                                         color='DarkSlateGrey')),
#                   selector=dict(mode='markers'))
fig.show()

In [213]:
df=c13.groupby('amount_yr0').agg({'yr0': 'sum', 'yr1': 'sum', 'retention_yr1': 'mean'}).reset_index()
df.loc[:,'group22110']=pd.qcut(df.index, q=22110, labels=False)

In [214]:
dfc=df.groupby('group22110')['amount_yr0']

In [215]:
dfc1=df.assign(min=dfc.transform(min), max=dfc.transform(max))

In [216]:
dfc1['group_range']=dfc1['min'].astype(str) + " - " + dfc1['max'].astype(str)

In [217]:
dfc1['comparative_retention']=np.where(dfc1['retention_yr1']> 0.19411439408377568,"higher",'lower')

In [218]:
dfc1

amount_yr0   yr0  yr1  retention_yr1  group22110        min        max  \
0            0.40     1    0       0.000000           0       0.40       0.40   
1            1.00  9492  380       0.040034           1       1.00       1.00   
2            1.02     1    1       1.000000           2       1.02       1.02   
3            1.15     1    0       0.000000           3       1.15       1.15   
4            1.19     1    1       1.000000           4       1.19       1.19   
...           ...   ...  ...            ...         ...        ...        ...   
22105    90140.60     1    1       1.000000       22105   90140.60   90140.60   
22106    94901.50     1    1       1.000000       22106   94901.50   94901.50   
22107   113360.94     1    1       1.000000       22107  113360.94  113360.94   
22108   163192.85     1    1       1.000000       22108  163192.85  163192.85   
22109   442794.38     1    1       1.000000       22109  442794.38  442794.38   

                 group_range comparative_retention  
0                  0.4 - 0.4                 lower  
1                  1.0 - 1.0                 lower  
2                1.02 - 1.02                higher  
3                1.15 - 1.15                 lower  
4                1.19 - 1.19                higher  
...                      ...                   ...  
22105      90140.6 - 90140.6                higher  
22106      94901.5 - 94901.5                higher  
22107  113360.94 - 113360.94                higher  
22108  163192.85 - 163192.85                higher  
22109  442794.38 - 442794.38                higher  

[22110 rows x 9 columns]

In [220]:
dfc1.comparative_retention.value_counts(normalize=True)

lower     0.516011
higher    0.483989
Name: comparative_retention, dtype: float64

In [184]:
#11055 groups
c13.loc[:,'group11055']=pd.qcut(c13.index, q=11055, labels=False)

C:\Users\erinm\Anaconda3\lib\site-packages\pandas\core\indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\erinm\Anaconda3\lib\site-packages\pandas\core\indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [185]:
df=c13.groupby('group11055').agg({'yr0': 'sum', 'yr1': 'sum', 'retention_yr1': 'mean'}).reset_index()
df.loc[:,'group11055']=pd.qcut(df.index, q=11055, labels=False)

In [186]:
df

group11055  yr0  yr1  retention_yr1
0               0   29    0       0.000000
1               1   29    3       0.103448
2               2   29    0       0.000000
3               3   29    1       0.034483
4               4   29    2       0.068966
...           ...  ...  ...            ...
11050       11050   29   20       0.689655
11051       11051   29   19       0.655172
11052       11052   29   10       0.344828
11053       11053   29   13       0.448276
11054       11054   29   23       0.793103

[11055 rows x 4 columns]

In [187]:
dfc=c13.groupby('group11055')['amount_yr0']

In [188]:
dfc1=df.assign(min=dfc.transform(min), max=dfc.transform(max))

In [189]:
dfc1=df.assign(min=dfc.transform(min), max=dfc.transform(max))

In [190]:
dfc1['comparative_retention']=np.where(dfc1['retention_yr1']> 0.19411439408377568,"higher",'lower')

In [191]:
df=c13.groupby(['group11055']).agg({'yr0':'sum','yr1':'sum','retention_yr1':'mean'}).reset_index()

In [193]:
dfc1.comparative_retention.value_counts(normalize=True)

lower     0.592311
higher    0.407689
Name: comparative_retention, dtype: float64

In [225]:
dfc1

amount_yr0   yr0  yr1  retention_yr1  group22110        min        max  \
0            0.40     1    0       0.000000           0       0.40       0.40   
1            1.00  9492  380       0.040034           1       1.00       1.00   
2            1.02     1    1       1.000000           2       1.02       1.02   
3            1.15     1    0       0.000000           3       1.15       1.15   
4            1.19     1    1       1.000000           4       1.19       1.19   
...           ...   ...  ...            ...         ...        ...        ...   
22105    90140.60     1    1       1.000000       22105   90140.60   90140.60   
22106    94901.50     1    1       1.000000       22106   94901.50   94901.50   
22107   113360.94     1    1       1.000000       22107  113360.94  113360.94   
22108   163192.85     1    1       1.000000       22108  163192.85  163192.85   
22109   442794.38     1    1       1.000000       22109  442794.38  442794.38   

                 group_range comparative_retention  
0                  0.4 - 0.4                 lower  
1                  1.0 - 1.0                 lower  
2                1.02 - 1.02                higher  
3                1.15 - 1.15                 lower  
4                1.19 - 1.19                higher  
...                      ...                   ...  
22105      90140.6 - 90140.6                higher  
22106      94901.5 - 94901.5                higher  
22107  113360.94 - 113360.94                higher  
22108  163192.85 - 163192.85                higher  
22109  442794.38 - 442794.38                higher  

[22110 rows x 9 columns]

In [232]:
old_list=c13.retention_yr1.tolist()

In [233]:
new_list = []
for value in old_list:
    if new_list and new_list[-1][0] == value:
        new_list[-1].append(value)
    else:
        new_list.append([value])

In [234]:
len(new_list)

91804

In [207]:
old_list=c13.amount_yr0.tolist()

In [229]:
len(old_list)

22110

In [235]:
new_list

[[0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0],
 [1.0],
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
 [1.0],
 [0.0, 0.0, 0.0, 0.0, 0.0],
 [1.0],
 [0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0],
 [1.0],
 [0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0],
 [1.0],
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
 [1.0],
 [0.0, 0.0, 0.0, 0.0],

In [231]:
c13

id    cohort  yr0  yr1  amount_yr0  \
5        69a7c6fed3094256c371fdd946585c15  cohort13    1    0        0.40   
8        2bb12d73c1b7859ad4e045ad455a03c3  cohort13    1    0        1.00   
9        54738e4163f3a49cc6f405c1ef221b26  cohort13    1    0        1.00   
11       e9c19a42c4965f0f91262bd56ff98cda  cohort13    1    0        1.00   
12       a614620bb7ac42c58e6740bdddf420e9  cohort13    1    0        1.00   
...                                   ...       ...  ...  ...         ...   
1876458  2144d56b1947ebb26a19e7f1d07c970a  cohort13    1    1    90140.60   
1876459  96c4f21513cd8962acb147ab384e6434  cohort13    1    1    94901.50   
1876463  0e01e632606c230914fe73c2d2ccead3  cohort13    1    1   113360.94   
1876465  8f70fc7370842e0709cd9af3d29b4b0b  cohort13    1    1   163192.85   
1876466  a0e1d358aa17745ff3d3f4e4909356f3  cohort13    1    1   442794.38   

         amount_yr1  retention_yr1  group1024  group2048  group4096  \
5              0.00            0.0          0          0          0   
8              0.00            0.0          0          0          0   
9              0.00            0.0          0          0          0   
11             0.00            0.0          0          0          0   
12             0.00            0.0          0          0          0   
...             ...            ...        ...        ...        ...   
1876458   159344.38            1.0       1023       2047       4095   
1876459   215995.85            1.0       1023       2047       4095   
1876463    77656.30            1.0       1023       2047       4095   
1876465    30893.09            1.0       1023       2047       4095   
1876466   570161.90            1.0       1023       2047       4095   

         group8192  group11055  
5                0           0  
8                0           0  
9                0           0  
11               0           0  
12               0           0  
...            ...         ...  
1876458       8191       11054  
1876459       8191       11054  
1876463       8191       11054  
1876465       8191       11054  
1876466       8191       11054  

[320069 rows x 12 columns]